In [1]:
!pip install datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 542.0/542.0 kB 8.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 16.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 25.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 18.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 401.2/401.2 kB 40.2 MB/s eta 0:00:00
  Attempting uninstall: huggingface-hub
    Found existing installation: huggingface-hub 0.20.3
    Uninstalling huggingface-hub-0.20.3:
      Successfully uninstalled huggingface-hub-0.20.3


Cargando el dataset

In [2]:
import torch
from torchvision import transforms
from torch.utils.data import Dataset, DataLoader
import torchvision.models as models
import numpy as np
from PIL import Image
import io
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
import torch
import torch.nn as nn

In [3]:
from datasets import load_dataset

dataset = load_dataset("huggan/wikiart")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Resolving data files:   0%|          | 0/72 [00:00<?, ?it/s]

Generating train split:   0%|          | 0/81444 [00:00<?, ? examples/s]

Loading dataset shards:   0%|          | 0/45 [00:00<?, ?it/s]

Prepando los datos

In [4]:
dataset_df = dataset['train'].to_pandas()
dataset_clean_df = dataset_df[(dataset_df['artist'] != 0) & (dataset_df['genre'] != 10)]
dataset_clean_df['image'] = dataset_clean_df['image'].apply(lambda x: x['bytes'])
dataset_clean_df.head(5)

<ipython-input-4-3009df837349>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataset_clean_df['image'] = dataset_clean_df['image'].apply(lambda x: x['bytes'])


image  artist  genre  style
0  b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x01...      22      4     21
1  b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...      20      7      4
2  b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...      16      6     20
3  b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...      17      2     12
5  b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...       1      2      3

In [5]:
X = dataset_clean_df['image']
y_artist = dataset_clean_df['artist']
y_genre = dataset_clean_df['genre']
y_style = dataset_clean_df['style']


def prepare_datasets(X, y, test_size=0.2, val_size=0.25):
    X_train_val, X_test, y_train_val, y_test = train_test_split(X, y, test_size=test_size, random_state=42)
    val_size_adjusted = val_size / (1 - test_size)
    X_train, X_val, y_train, y_val = train_test_split(X_train_val, y_train_val, test_size=val_size_adjusted, random_state=42)
    return X_train, X_val, X_test, y_train, y_val, y_test

# Split data for 'artist'
X_train_artist, X_val_artist, X_test_artist, y_train_artist, y_val_artist, y_test_artist = prepare_datasets(X, y_artist)

# Split data for 'genre'
X_train_genre, X_val_genre, X_test_genre, y_train_genre, y_val_genre, y_test_genre = prepare_datasets(X, y_genre)

# Split data for 'style'
X_train_style, X_val_style, X_test_style, y_train_style, y_val_style, y_test_style = prepare_datasets(X, y_style)


In [6]:
X_train_artist

33986    b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
23090    b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
14369    b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
15795    b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
37711    b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
                               ...                        
20087    b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
51162    b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
6127     b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
44785    b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
30263    b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
Name: image, Length: 20273, dtype: object

In [7]:
print(X_train_artist.shape)
print(X_val_artist.shape)
print(X_test_artist.shape)
print(y_train_artist.shape)
print(y_val_artist.shape)
print(y_test_artist.shape)

(20273,)
(9215,)
(7373,)
(20273,)
(9215,)
(7373,)


In [25]:
augmentation_transforms = transforms.Compose([
    transforms.RandomHorizontalFlip(),
    transforms.RandomRotation(20),
    transforms.ColorJitter(brightness=0.2, contrast=0.2, saturation=0.2),
    transforms.RandomResizedCrop(224, scale=(0.8, 1.0), ratio=(0.9, 1.1)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

class AugmentedImageDataset(Dataset):
    def __init__(self, X, y, transform=None):
        # Make sure X is a reset pandas Series
        self.X = X.reset_index(drop=True)
        self.y = y.reset_index(drop=True)
        self.transform = transform

    def __len__(self):
        return len(self.X)

    def __getitem__(self, idx):
        # Check if the index is within range
        if idx >= len(self.X):
            raise IndexError(f"Index {idx} is out of bounds for dataset with length {len(self.X)}")
        # Read the image from bytes
        image = Image.open(io.BytesIO(self.X[idx]))
        # Apply transformations if any
        if self.transform:
            image = self.transform(image)
        # Return the image and its corresponding label
        return image, self.y[idx]


# Create an augmented dataset for training
augmented_train_dataset = AugmentedImageDataset(X_train_artist, y_train_artist, transform=augmentation_transforms)
train_loader_artist = DataLoader(augmented_train_dataset, batch_size=100, shuffle=True)

# Create augmented datasets for 'genre' and 'style'
augmented_train_dataset_genre = AugmentedImageDataset(X_train_genre, y_train_genre, transform=augmentation_transforms)
train_loader_genre = DataLoader(augmented_train_dataset_genre, batch_size=700, shuffle=True)

augmented_train_dataset_style = AugmentedImageDataset(X_train_style, y_train_style, transform=augmentation_transforms)
train_loader_style = DataLoader(augmented_train_dataset_style, batch_size=100, shuffle=True)




In [26]:
augmented_train_dataset.X.shape

(20273,)

In [10]:
type(augmented_train_dataset.X)

pandas.core.series.Series

In [11]:
augmented_train_dataset.X

0        b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
1        b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
2        b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
3        b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
4        b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
                               ...                        
20268    b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
20269    b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
20270    b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
20271    b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
20272    b'\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x01\x00...
Name: image, Length: 20273, dtype: object

In [12]:
augmented_train_dataset.y.shape

(20273,)

In [13]:
augmented_train_dataset.y

0         36
1        110
2         22
3         12
4        115
        ... 
20268     91
20269    100
20270     16
20271     95
20272     39
Name: artist, Length: 20273, dtype: int64

In [14]:

print(len(np.unique(augmented_train_dataset.y)))


128


In [27]:
# Create an augmented dataset for validation
augmented_validation_dataset = AugmentedImageDataset(X_val_artist, y_val_artist, transform=augmentation_transforms)
validation_loader_artist = DataLoader(augmented_validation_dataset, batch_size=32, shuffle=True)

# Create augmented datasets for 'genre' and 'style'
augmented_validation_dataset_genre = AugmentedImageDataset(X_val_genre, y_val_genre, transform=augmentation_transforms)
validation_loader_genre = DataLoader(augmented_validation_dataset_genre, batch_size=700, shuffle=True)

augmented_validation_dataset_style = AugmentedImageDataset(X_val_style, y_val_style, transform=augmentation_transforms)
validation_loader_style = DataLoader(augmented_validation_dataset_style, batch_size=32, shuffle=True)

In [28]:
# Create an augmented dataset for testing
augmented_test_dataset = AugmentedImageDataset(X_test_artist, y_test_artist, transform=augmentation_transforms)
test_loader_artist = DataLoader(augmented_test_dataset, batch_size=32, shuffle=True)

# Create augmented datasets for 'genre' and 'style'
augmented_test_dataset_genre = AugmentedImageDataset(X_test_genre, y_test_genre, transform=augmentation_transforms)
test_loader_genre = DataLoader(augmented_test_dataset_genre, batch_size=700, shuffle=True)

augmented_test_dataset_style = AugmentedImageDataset(X_test_style, y_test_style, transform=augmentation_transforms)
test_loader_style = DataLoader(augmented_test_dataset_style, batch_size=32, shuffle=True)

In [17]:
# prompt: print how many different values does y_train_artist have

print(len(np.unique(y_train_artist)))
print(len(np.unique(y_train_genre)))
print(len(np.unique(y_train_style)))


128
10
25


In [18]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print(f"Entrenando en dispositivo: {device}")

Entrenando en dispositivo: cuda:0


Artist

In [19]:


class CustomAlexNet(nn.Module):
    def __init__(self, num_classes):
        super(CustomAlexNet, self).__init__()
        self.alexnet = models.alexnet(pretrained=True)
        # Freeze the features layers
        for param in self.alexnet.features.parameters():
            param.requires_grad = False
        # Replace the classifier layer
        num_features = self.alexnet.classifier[6].in_features
        self.alexnet.classifier[6] = nn.Linear(num_features, num_classes)

    def forward(self, x):
        return self.alexnet(x)





Genre

In [34]:
class CustomResNet18(nn.Module):
    def __init__(self, num_classes):
        super(CustomResNet18, self).__init__()
        self.resnet18 = models.resnet18(pretrained=True)

        # Freeze all layers in the network
        for param in self.resnet18.parameters():
            param.requires_grad = False

        # Replace the final fully connected layer
        num_features = self.resnet18.fc.in_features
        self.resnet18.fc = nn.Linear(num_features, num_classes)
    def forward(self, x):
        x = self.resnet18(x)
        return x



Style

In [21]:
class VGGClassifier(nn.Module):
    def __init__(self, num_classes):
        super(VGGClassifier, self).__init__()
        self.vgg = models.vgg16(pretrained=True)

        for param in self.vgg.parameters():
            param.requires_grad = False

        num_features = self.vgg.classifier[6].in_features
        self.vgg.classifier[6] = nn.Linear(num_features, num_classes)

    def forward(self, x):
        return self.vgg(x)

In [35]:
num_artist_classes = 129
num_genre_classes = 10
num_style_classes = 25

model_artist = CustomAlexNet(num_artist_classes)
model_genre = CustomResNet18(num_genre_classes)
model_style = VGGClassifier(num_style_classes)

In [36]:
import torch.optim as optim
from tqdm import tqdm

# Loss function and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(filter(lambda p: p.requires_grad, model_genre.parameters()), lr=0.001)


def train_one_epoch(model, dataloader, optimizer, criterion, device):
    model.train()
    running_loss = 0.0
    correct = 0
    total = 0
    for inputs, labels in tqdm(dataloader, desc="Training", leave=False):
        inputs, labels = inputs.to(device), labels.to(device)
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        running_loss += loss.item()

        _, predicted = torch.max(outputs.data, 1)
        total += labels.size(0)
        correct += (predicted == labels).sum().item()

    accuracy = 100 * correct / total
    return running_loss / len(dataloader), accuracy



def validate(model, dataloader, criterion, device):
    model.eval()
    running_loss = 0.0
    # Wrap the dataloader with tqdm for a progress bar
    with torch.no_grad():
        for inputs, labels in tqdm(dataloader, desc="Validation", leave=False):
            inputs, labels = inputs.to(device), labels.to(device)
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            running_loss += loss.item()
    return running_loss / len(dataloader)


# Training loop
epochs = 10
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model_genre.to(device)
best_accuracy = 0.0

for epoch in tqdm(range(epochs), desc="Epochs"):
    train_loss, train_accuracy = train_one_epoch(model_genre, train_loader_genre, optimizer, criterion, device)
    val_loss = validate(model_genre, validation_loader_genre, criterion, device)
    print(f'Epoch {epoch+1}/{epochs}, Train Loss: {train_loss:.4f}, Train Accuracy: {train_accuracy:.2f}%, Val Loss: {val_loss:.4f}')

    if train_accuracy > best_accuracy:
        best_accuracy = train_accuracy
        torch.save(model_genre.state_dict(), 'best_model_genre.pth')
        print(f"Saved new best model with accuracy: {train_accuracy:.2f}%")


Training: 100%|██████████| 29/29 [41:50<00:00, 85.74s/it]
                                                         
Epochs:  10%|█         | 1/10 [1:00:43<9:06:27, 3643.06s/it]

Epoch 1/10, Train Loss: 1.6777, Train Accuracy: 45.63%, Val Loss: 1.3232
Saved new best model with accuracy: 45.63%



Training: 100%|██████████| 29/29 [41:49<00:00, 85.01s/it]
                                                         
Epochs:  20%|██        | 2/10 [2:01:20<8:05:16, 3639.54s/it]

Epoch 2/10, Train Loss: 1.1849, Train Accuracy: 60.89%, Val Loss: 1.0962
Saved new best model with accuracy: 60.89%



Training: 100%|██████████| 29/29 [41:43<00:00, 85.69s/it]
                                                         
Epochs:  30%|███       | 3/10 [3:02:10<7:05:11, 3644.52s/it]

...

Epoch 8/10, Train Loss: 0.8772, Train Accuracy: 69.49%, Val Loss: 0.8992
Saved new best model with accuracy: 69.49%



Training: 100%|██████████| 29/29 [39:34<00:00, 81.66s/it]
                                                         
Epochs:  90%|█████████ | 9/10 [8:42:48<57:06, 3426.39s/it]  

Epoch 9/10, Train Loss: 0.8672, Train Accuracy: 69.81%, Val Loss: 0.8830
Saved new best model with accuracy: 69.81%



Training: 100%|██████████| 29/29 [40:10<00:00, 83.29s/it]
                                                         
Epochs: 100%|██████████| 10/10 [9:41:23<00:00, 3488.39s/it]

Epoch 10/10, Train Loss: 0.8608, Train Accuracy: 69.68%, Val Loss: 0.8949


In [37]:
# Loss function and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(filter(lambda p: p.requires_grad, model_genre.parameters()), lr=0.001)


def train_one_epoch(model, dataloader, optimizer, criterion, device):
    model.train()
    running_loss = 0.0
    correct = 0
    total = 0
    for inputs, labels in tqdm(dataloader, desc="Training", leave=False):
        inputs, labels = inputs.to(device), labels.to(device)
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        running_loss += loss.item()

        _, predicted = torch.max(outputs.data, 1)
        total += labels.size(0)
        correct += (predicted == labels).sum().item()

    accuracy = 100 * correct / total
    return running_loss / len(dataloader), accuracy



def validate(model, dataloader, criterion, device):
    model.eval()
    running_loss = 0.0
    # Wrap the dataloader with tqdm for a progress bar
    with torch.no_grad():
        for inputs, labels in tqdm(dataloader, desc="Validation", leave=False):
            inputs, labels = inputs.to(device), labels.to(device)
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            running_loss += loss.item()
    return running_loss / len(dataloader)


# Training loop
epochs = 10
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model_style.to(device)
best_accuracy = 0.0

for epoch in tqdm(range(epochs), desc="Epochs"):
    train_loss, train_accuracy = train_one_epoch(model_style, train_loader_style, optimizer, criterion, device)
    val_loss = validate(model_style, validation_loader_style, criterion, device)
    print(f'Epoch {epoch+1}/{epochs}, Train Loss: {train_loss:.4f}, Train Accuracy: {train_accuracy:.2f}%, Val Loss: {val_loss:.4f}')

    if train_accuracy > best_accuracy:
        best_accuracy = train_accuracy
        torch.save(model_style.state_dict(), 'best_model_style.pth')
        print(f"Saved new best model with accuracy: {train_accuracy:.2f}%")


Epochs:   0%|          | 0/10 [00:12<?, ?it/s]


RuntimeError: CUDA error: device-side assert triggered
CUDA kernel errors might be asynchronously reported at some other API call, so the stacktrace below might be incorrect.
For debugging consider passing CUDA_LAUNCH_BLOCKING=1.
Compile with `TORCH_USE_CUDA_DSA` to enable device-side assertions.
